In [2]:
!git clone https://github.com/atikul-islam-sajib/CharlottWorks.git

Cloning into 'CharlottWorks'...
remote: Enumerating objects: 226, done.
remote: Counting objects: 100% (226/226), done.
remote: Compressing objects: 100% (157/157), done.
remote: Total 226 (delta 127), reused 160 (delta 61), pack-reused 0 (from 0)
Receiving objects: 100% (226/226), 2.02 MiB | 4.59 MiB/s, done.
Resolving deltas: 100% (127/127), done.


In [3]:
%cd CharlottWorks

/content/CharlottWorks


In [4]:
import torch
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device

device(type='cuda')

In [5]:
!pip install simpletransformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.4/42.4 kB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 4.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.3/44.3 kB 2.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 316.3/316.3 kB 13.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 31.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.6/8.6 MB 20.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.7/101.7 kB 6.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 13.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 11.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.9/6.9 MB 69.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.1/79.1 kB 6.7 MB/s eta 0:00:00
  

In [6]:
!pip install optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 364.4/364.4 kB 12.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.5/233.5 kB 16.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 6.1 MB/s eta 0:00:00


In [7]:
from simpletransformers.classification import ClassificationModel, ClassificationArgs
import pandas as pd
import re
from sklearn.model_selection import GroupShuffleSplit
import torch
from sklearn.metrics import mean_squared_error, f1_score, accuracy_score, classification_report, confusion_matrix
import optuna
import seaborn as sns
import matplotlib.pyplot as plt
import os
import json

In [8]:
df_train = pd.read_csv('./data/ground_truth_train.csv')
df_test = pd.read_csv('./data/ground_truth_test.csv')

In [9]:
df_train.shape, df_test.shape

((191, 15), (74, 15))

In [10]:
# assert that no documents from train are in test data
set(df_train['document']).intersection(set(df_test['document']))

set()

In [11]:
df_train.head()

document                                               text  \
0    1.txt  The diverse range of the members’ educational ...   
1   10.txt  Contributing to society by improving access to...   
2   10.txt  Contributing to society by improving access to...   
3  100.txt  Our water strategy focuses on working towards ...   
4  100.txt  Our water strategy focuses on working towards ...   

                                             keyword         event_trigger  \
0  25-74 [members’ educational and professional b...      75-83 [includes]   
1           140-170 [Ambition Zero Carbon programme]  125-135 [delivering]   
2                   59-83 [environmental protection]     27-36 [improving]   
3                           119-133 [water security]     111-118 [support]   
4                          0-18 [Our water strategy]       19-26 [focuses]   

  temporal_status  measurability event_factuality  kw_is_nsubj  kw_is_dobj  \
0         ongoing            1.0                _        False       False   
1         ongoing            2.0            3_max        False        True   
2         ongoing            1.0            3_max        False       False   
3         ongoing            2.0            0_low        False        True   
4         ongoing            1.0            3_max         True       False   

   kw_is_pobj   category                                         text_kw_et  \
0        True  situation  The diverse range of the members’ educational ...   
1       False     action  Contributing to society by improving access to...   
2       False     action  Contributing to society by improving access to...   
3       False     action  Our water strategy focuses on working towards ...   
4       False  situation  Our water strategy focuses on working towards ...   

                                             text_kw  \
0  The diverse range of the members’ educational ...   
1  Contributing to society by improving access to...   
2  Contributing to society by improving access to...   
3  Our water strategy focuses on working towards ...   
4  Our water strategy focuses on working towards ...   

  relation_time_specification relation_unit  
0                         NaN           NaN  
1                         NaN           NaN  
2                         NaN           NaN  
3                         NaN           NaN  
4                         NaN           NaN

In [12]:
df_train.head()

document                                               text  \
0    1.txt  The diverse range of the members’ educational ...   
1   10.txt  Contributing to society by improving access to...   
2   10.txt  Contributing to society by improving access to...   
3  100.txt  Our water strategy focuses on working towards ...   
4  100.txt  Our water strategy focuses on working towards ...   

                                             keyword         event_trigger  \
0  25-74 [members’ educational and professional b...      75-83 [includes]   
1           140-170 [Ambition Zero Carbon programme]  125-135 [delivering]   
2                   59-83 [environmental protection]     27-36 [improving]   
3                           119-133 [water security]     111-118 [support]   
4                          0-18 [Our water strategy]       19-26 [focuses]   

  temporal_status  measurability event_factuality  kw_is_nsubj  kw_is_dobj  \
0         ongoing            1.0                _        False       False   
1         ongoing            2.0            3_max        False        True   
2         ongoing            1.0            3_max        False       False   
3         ongoing            2.0            0_low        False        True   
4         ongoing            1.0            3_max         True       False   

   kw_is_pobj   category                                         text_kw_et  \
0        True  situation  The diverse range of the members’ educational ...   
1       False     action  Contributing to society by improving access to...   
2       False     action  Contributing to society by improving access to...   
3       False     action  Our water strategy focuses on working towards ...   
4       False  situation  Our water strategy focuses on working towards ...   

                                             text_kw  \
0  The diverse range of the members’ educational ...   
1  Contributing to society by improving access to...   
2  Contributing to society by improving access to...   
3  Our water strategy focuses on working towards ...   
4  Our water strategy focuses on working towards ...   

  relation_time_specification relation_unit  
0                         NaN           NaN  
1                         NaN           NaN  
2                         NaN           NaN  
3                         NaN           NaN  
4                         NaN           NaN

# Prepare Data for BERT

In [13]:
def extract_content_in_brackets(text):
    """
    Extracts and returns the content within the first pair of square brackets found in the given text.
    If no square brackets are found, returns an empty string.
    """
    text = str(text)
    match = re.search(r'\[(.*?)\]', text)
    if match:
        return match.group(1)
    else:
        return ""

df_train['event_trigger'] = df_train['event_trigger'].apply(extract_content_in_brackets)
df_test['event_trigger'] = df_test['event_trigger'].apply(extract_content_in_brackets)
df_train['keyword'] = df_train['keyword'].apply(extract_content_in_brackets)
df_test['keyword'] = df_test['keyword'].apply(extract_content_in_brackets)

In [14]:
# select relevant columns
df_train = df_train[['document', 'text', 'event_trigger', 'keyword', 'category']]
df_test = df_test[['document', 'text', 'event_trigger', 'keyword', 'category']]

In [15]:
def format_text(row):
    sentence = row['text'].replace(row['keyword'], f"[KEYWORD] {row['keyword']} [/KEYWORD]")
    sentence = sentence.replace(row['event_trigger'], f"[TRIGGER] {row['event_trigger']} [/TRIGGER]")
    return sentence

df_train['text'] = df_train.apply(format_text, axis=1)
df_test['text'] = df_test.apply(format_text, axis=1)

<ipython-input-15-4d14f909cf1d>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_train['text'] = df_train.apply(format_text, axis=1)
<ipython-input-15-4d14f909cf1d>:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_test['text'] = df_test.apply(format_text, axis=1)


In [16]:
# rename "category" to "label"
df_train = df_train.rename(columns={'category': 'label'})
df_test = df_test.rename(columns={'category': 'label'})

# Map labels to integers if necessary
label_mapping = {'action': 0, 'intention': 1, 'belief': 2, 'situation': 3}  # Update according to your labels
df_train['label'] = df_train['label'].map(label_mapping)
df_test['label'] = df_test['label'].map(label_mapping)

In [17]:
# Select only the necessary columns
df_train = df_train[['text', 'label']]
df_test = df_test[['text', 'label']]

In [18]:
X_train = df_train['text']
y_train = df_train['label']
X_test = df_test['text']
y_test = df_test['label']

In [19]:
set(df_train['label']), set(df_test['label'])

({0, 1, 2, 3}, {0, 1, 2, 3})

In [20]:
num_labels = len(df_train['label'].unique())
num_labels

4

In [21]:
df_train.head()

text  label
0  The diverse range of the [KEYWORD] members’ ed...      3
1  Contributing to society by improving access to...      0
2  Contributing to society by [TRIGGER] improving...      0
3  Our water strategy focuses on working towards ...      0
4  [KEYWORD] Our water strategy [/KEYWORD] [TRIGG...      3

In [22]:
X_train.shape

(191,)


# Hyperparameter Tuning Process

1. **Random Search (RandomizedSearchCV)**:
   - Initially, I performed hyperparameter tuning using **RandomizedSearchCV**, which explores a wide range of hyperparameter combinations by sampling randomly within the defined search space. This step helped to quickly identify a general region in the hyperparameter space where the model performs well.

2. **Grid Search (GridSearchCV)**:
   - Based on the promising results from **RandomizedSearchCV**, I refined the hyperparameter search using **GridSearchCV**. This method systematically evaluates all possible combinations of hyperparameters in a narrower, focused search space, leading to a more precise selection of optimal parameters.

3. **Optuna Optimization**:
   - Finally, I utilized the results from **GridSearchCV** to set the initial conditions for **Optuna**, a state-of-the-art optimization framework. Optuna conducted a more granular and efficient search by employing advanced optimization algorithms (e.g., Tree-structured Parzen Estimator, TPE), further fine-tuning the hyperparameters to achieve the best performance.

## ROBERTA

In [ ]:
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import numpy as np
import pandas as pd
from simpletransformers.classification import ClassificationModel, ClassificationArgs

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5
model_args.learning_rate = 8e-5
model_args.train_batch_size = 8
model_args.eval_batch_size = 8
model_args.max_seq_length = 512
model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "roberta", "roberta-base",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )
    model.train_model(train_data[['text', 'label']])

    # Evaluate the model on the validation set
    result, model_outputs, _ = model.eval_model(val_data[['text', 'label']])

    # Get true and predicted labels
    true_labels = val_data['label'].values
    predicted_labels = np.argmax(model_outputs, axis=1)

    # Calculate metrics for this fold
    accuracy = accuracy_score(true_labels, predicted_labels)
    precision = precision_score(true_labels, predicted_labels, average='weighted')
    recall = recall_score(true_labels, predicted_labels, average='weighted')
    f1 = f1_score(true_labels, predicted_labels, average='weighted')

    # Append metrics to lists
    accuracy_scores.append(accuracy)
    precision_scores.append(precision)
    recall_scores.append(recall)
    f1_scores.append(f1)

    print(f"Fold {fold + 1} Metrics:")
    print(f"Accuracy: {accuracy}")
    print(f"Precision: {precision}")
    print(f"Recall: {recall}")
    print(f"F1 Score: {f1}")

# Calculate and print average metrics across all folds
print("\nOverall Metrics Across All Folds:")
print(f"Average Accuracy: {np.mean(accuracy_scores)}")
print(f"Average Precision: {np.mean(precision_scores)}")
print(f"Average Recall: {np.mean(recall_scores)}")
print(f"Average F1 Score: {np.mean(f1_scores)}")

Starting Fold 1


Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:882: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = amp.GradScaler()


...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/3 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


Fold 5 Metrics:
Accuracy: 0.625
Precision: 0.6458333333333334
Recall: 0.625
F1 Score: 0.6071428571428571

Overall Metrics Across All Folds:
Average Accuracy: 0.6519999999999999
Average Precision: 0.6573373015873016
Average Recall: 0.6519999999999999
Average F1 Score: 0.6346468253968254


In [ ]:
'''
Overall Metrics Across All Folds:
Average Accuracy: 0.6519999999999999
Average Precision: 0.6573373015873016
Average Recall: 0.6519999999999999
Average F1 Score: 0.6346468253968254
'''

## BERT

In [ ]:
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import numpy as np
import pandas as pd
from simpletransformers.classification import ClassificationModel, ClassificationArgs

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5
model_args.learning_rate = 8e-6
model_args.train_batch_size = 1
model_args.eval_batch_size = 16
model_args.max_seq_length = 512

model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "bert", "bert-base-uncased",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )
    model.train_model(train_data[['text', 'label']])

    # Evaluate the model on the validation set
    result, model_outputs, _ = model.eval_model(val_data[['text', 'label']])

    # Get true and predicted labels
    true_labels = val_data['label'].values
    predicted_labels = np.argmax(model_outputs, axis=1)

    # Calculate metrics for this fold
    accuracy = accuracy_score(true_labels, predicted_labels)
    precision = precision_score(true_labels, predicted_labels, average='weighted')
    recall = recall_score(true_labels, predicted_labels, average='weighted')
    f1 = f1_score(true_labels, predicted_labels, average='weighted')

    # Append metrics to lists
    accuracy_scores.append(accuracy)
    precision_scores.append(precision)
    recall_scores.append(recall)
    f1_scores.append(f1)

    print(f"Fold {fold + 1} Metrics:")
    print(f"Accuracy: {accuracy}")
    print(f"Precision: {precision}")
    print(f"Recall: {recall}")
    print(f"F1 Score: {f1}")

# Calculate and print average metrics across all folds
print("\nOverall Metrics Across All Folds:")
print(f"Average Accuracy: {np.mean(accuracy_scores)}")
print(f"Average Precision: {np.mean(precision_scores)}")
print(f"Average Recall: {np.mean(recall_scores)}")
print(f"Average F1 Score: {np.mean(f1_scores)}")

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Starting Fold 1


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

...

0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/2 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


Fold 5 Metrics:
Accuracy: 0.5416666666666666
Precision: 0.4847222222222222
Recall: 0.5416666666666666
F1 Score: 0.4545454545454546

Overall Metrics Across All Folds:
Average Accuracy: 0.612
Average Precision: 0.5584982517482517
Average Recall: 0.612
Average F1 Score: 0.5589050024050024


/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


## BERT

In [ ]:
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import numpy as np
import pandas as pd
from simpletransformers.classification import ClassificationModel, ClassificationArgs

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5  # Moderate number of epochs
model_args.learning_rate = 3e-5  # Start with a standard learning rate
model_args.train_batch_size = 4  # Larger batches for stability
model_args.eval_batch_size = 4  # Match training batch size
model_args.max_seq_length = 512  # Maximum length


model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "distilbert", "distilbert-base-uncased",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )
    model.train_model(train_data[['text', 'label']])

    # Evaluate the model on the validation set
    result, model_outputs, _ = model.eval_model(val_data[['text', 'label']])

    # Get true and predicted labels
    true_labels = val_data['label'].values
    predicted_labels = np.argmax(model_outputs, axis=1)

    # Calculate metrics for this fold
    accuracy = accuracy_score(true_labels, predicted_labels)
    precision = precision_score(true_labels, predicted_labels, average='weighted')
    recall = recall_score(true_labels, predicted_labels, average='weighted')
    f1 = f1_score(true_labels, predicted_labels, average='weighted')

    # Append metrics to lists
    accuracy_scores.append(accuracy)
    precision_scores.append(precision)
    recall_scores.append(recall)
    f1_scores.append(f1)

    print(f"Fold {fold + 1} Metrics:")
    print(f"Accuracy: {accuracy}")
    print(f"Precision: {precision}")
    print(f"Recall: {recall}")
    print(f"F1 Score: {f1}")

# Calculate and print average metrics across all folds
print("\nOverall Metrics Across All Folds:")
print(f"Average Accuracy: {np.mean(accuracy_scores)}")
print(f"Average Precision: {np.mean(precision_scores)}")
print(f"Average Recall: {np.mean(recall_scores)}")
print(f"Average F1 Score: {np.mean(f1_scores)}")

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Starting Fold 1


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/6 [00:00<?, ?it/s]

Fold 5 Metrics:
Accuracy: 0.625
Precision: 0.6041666666666666
Recall: 0.625
F1 Score: 0.5607142857142856

Overall Metrics Across All Folds:
Average Accuracy: 0.7013333333333334
Average Precision: 0.7242478632478633
Average Recall: 0.7013333333333334
Average F1 Score: 0.6774454461946722


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


## DistilBERT

In [ ]:
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import numpy as np
import pandas as pd
from simpletransformers.classification import ClassificationModel, ClassificationArgs

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5  # Moderate number of epochs
model_args.learning_rate = 3e-5  # Start with a standard learning rate
model_args.train_batch_size = 2  # Larger batches for stability
model_args.eval_batch_size = 8  # Match training batch size
model_args.max_seq_length = 512  # Maximum length


model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "distilbert", "distilbert-base-uncased",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )
    model.train_model(train_data[['text', 'label']])

    # Evaluate the model on the validation set
    result, model_outputs, _ = model.eval_model(val_data[['text', 'label']])

    # Get true and predicted labels
    true_labels = val_data['label'].values
    predicted_labels = np.argmax(model_outputs, axis=1)

    # Calculate metrics for this fold
    accuracy = accuracy_score(true_labels, predicted_labels)
    precision = precision_score(true_labels, predicted_labels, average='weighted')
    recall = recall_score(true_labels, predicted_labels, average='weighted')
    f1 = f1_score(true_labels, predicted_labels, average='weighted')

    # Append metrics to lists
    accuracy_scores.append(accuracy)
    precision_scores.append(precision)
    recall_scores.append(recall)
    f1_scores.append(f1)

    print(f"Fold {fold + 1} Metrics:")
    print(f"Accuracy: {accuracy}")
    print(f"Precision: {precision}")
    print(f"Recall: {recall}")
    print(f"F1 Score: {f1}")

# Calculate and print average metrics across all folds
print("\nOverall Metrics Across All Folds:")
print(f"Average Accuracy: {np.mean(accuracy_scores)}")
print(f"Average Precision: {np.mean(precision_scores)}")
print(f"Average Recall: {np.mean(recall_scores)}")
print(f"Average F1 Score: {np.mean(f1_scores)}")

Starting Fold 1


Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:882: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = amp.GradScaler()


...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/3 [00:00<?, ?it/s]

Fold 5 Metrics:
Accuracy: 0.7083333333333334
Precision: 0.7215277777777778
Recall: 0.7083333333333334
F1 Score: 0.6932234432234433

Overall Metrics Across All Folds:
Average Accuracy: 0.7266666666666667
Average Precision: 0.7426706349206349
Average Recall: 0.7266666666666667
Average F1 Score: 0.718359616991196


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


## ALBERT

In [ ]:
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import numpy as np
import pandas as pd
from simpletransformers.classification import ClassificationModel, ClassificationArgs

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5  # Moderate number of epochs
model_args.learning_rate = 8e-6  # Start with a standard learning rate
model_args.train_batch_size = 2  # Larger batches for stability
model_args.eval_batch_size = 16  # Match training batch size
model_args.max_seq_length = 512  # Maximum length


model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "albert", "albert-base-v2",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )
    model.train_model(train_data[['text', 'label']])

    # Evaluate the model on the validation set
    result, model_outputs, _ = model.eval_model(val_data[['text', 'label']])

    # Get true and predicted labels
    true_labels = val_data['label'].values
    predicted_labels = np.argmax(model_outputs, axis=1)

    # Calculate metrics for this fold
    accuracy = accuracy_score(true_labels, predicted_labels)
    precision = precision_score(true_labels, predicted_labels, average='weighted')
    recall = recall_score(true_labels, predicted_labels, average='weighted')
    f1 = f1_score(true_labels, predicted_labels, average='weighted')

    # Append metrics to lists
    accuracy_scores.append(accuracy)
    precision_scores.append(precision)
    recall_scores.append(recall)
    f1_scores.append(f1)

    print(f"Fold {fold + 1} Metrics:")
    print(f"Accuracy: {accuracy}")
    print(f"Precision: {precision}")
    print(f"Recall: {recall}")
    print(f"F1 Score: {f1}")

# Calculate and print average metrics across all folds
print("\nOverall Metrics Across All Folds:")
print(f"Average Accuracy: {np.mean(accuracy_scores)}")
print(f"Average Precision: {np.mean(precision_scores)}")
print(f"Average Recall: {np.mean(recall_scores)}")
print(f"Average F1 Score: {np.mean(f1_scores)}")

Some weights of AlbertForSequenceClassification were not initialized from the model checkpoint at albert-base-v2 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Starting Fold 1


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/2 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


Fold 5 Metrics:
Accuracy: 0.6666666666666666
Precision: 0.6916666666666668
Recall: 0.6666666666666666
F1 Score: 0.6444215506715506

Overall Metrics Across All Folds:
Average Accuracy: 0.6193333333333333
Average Precision: 0.6568040404040404
Average Recall: 0.6193333333333333
Average F1 Score: 0.6027162599182723


## DistilBERT - Verify with Macro as well

In [ ]:
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import numpy as np
import pandas as pd
from simpletransformers.classification import ClassificationModel, ClassificationArgs

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5  # Moderate number of epochs
model_args.learning_rate = 3e-5  # Start with a standard learning rate
model_args.train_batch_size = 2  # Larger batches for stability
model_args.eval_batch_size = 8  # Match training batch size
model_args.max_seq_length = 512  # Maximum length


model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "distilbert", "distilbert-base-uncased",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )
    model.train_model(train_data[['text', 'label']])

    # Evaluate the model on the validation set
    result, model_outputs, _ = model.eval_model(val_data[['text', 'label']])

    # Get true and predicted labels
    true_labels = val_data['label'].values
    predicted_labels = np.argmax(model_outputs, axis=1)

    # Calculate metrics for this fold
    accuracy = accuracy_score(true_labels, predicted_labels)
    precision = precision_score(true_labels, predicted_labels, average='macro')
    recall = recall_score(true_labels, predicted_labels, average='macro')
    f1 = f1_score(true_labels, predicted_labels, average='macro')

    # Append metrics to lists
    accuracy_scores.append(accuracy)
    precision_scores.append(precision)
    recall_scores.append(recall)
    f1_scores.append(f1)

    print(f"Fold {fold + 1} Metrics:")
    print(f"Accuracy: {accuracy}")
    print(f"Precision: {precision}")
    print(f"Recall: {recall}")
    print(f"F1 Score: {f1}")

# Calculate and print average metrics across all folds
print("\nOverall Metrics Across All Folds:")
print(f"Average Accuracy: {np.mean(accuracy_scores)}")
print(f"Average Precision: {np.mean(precision_scores)}")
print(f"Average Recall: {np.mean(recall_scores)}")
print(f"Average F1 Score: {np.mean(f1_scores)}")

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Starting Fold 1


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/3 [00:00<?, ?it/s]

Fold 5 Metrics:
Accuracy: 0.625
Precision: 0.6249999999999999
Recall: 0.6597222222222222
F1 Score: 0.5909090909090908

Overall Metrics Across All Folds:
Average Accuracy: 0.6936666666666667
Average Precision: 0.7275946275946275
Average Recall: 0.6907539682539683
Average F1 Score: 0.6702829196946845


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


In [ ]:
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import numpy as np
import pandas as pd
from simpletransformers.classification import ClassificationModel, ClassificationArgs

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5  # Moderate number of epochs
model_args.learning_rate = 3e-5  # Start with a standard learning rate
model_args.train_batch_size = 2  # Larger batches for stability
model_args.eval_batch_size = 8  # Match training batch size
model_args.max_seq_length = 512  # Maximum length

model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]  # This is only for training validation, not for metrics

    # Create and train the model
    model = ClassificationModel(
        "distilbert", "distilbert-base-uncased",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )
    model.train_model(train_data[['text', 'label']])

    # Evaluate the model on the test set (df_test)
    result, model_outputs, _ = model.eval_model(df_test[['text', 'label']])

    # Get true and predicted labels
    true_labels = df_test['label'].values
    predicted_labels = np.argmax(model_outputs, axis=1)

    # Calculate metrics for this fold on df_test
    accuracy = accuracy_score(true_labels, predicted_labels)
    precision = precision_score(true_labels, predicted_labels, average='macro')
    recall = recall_score(true_labels, predicted_labels, average='macro')
    f1 = f1_score(true_labels, predicted_labels, average='macro')

    # Append metrics to lists
    accuracy_scores.append(accuracy)
    precision_scores.append(precision)
    recall_scores.append(recall)
    f1_scores.append(f1)

    print(f"Fold {fold + 1} Metrics on Test Set:")
    print(f"Accuracy: {accuracy}")
    print(f"Precision: {precision}")
    print(f"Recall: {recall}")
    print(f"F1 Score: {f1}")

# Calculate and print average metrics across all folds
print("\nOverall Metrics Across All Folds (Test Set):")
print(f"Average Accuracy: {np.mean(accuracy_scores)}")
print(f"Average Precision: {np.mean(precision_scores)}")
print(f"Average Recall: {np.mean(recall_scores)}")
print(f"Average F1 Score: {np.mean(f1_scores)}")

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Starting Fold 1


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/10 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


Fold 5 Metrics on Test Set:
Accuracy: 0.5675675675675675
Precision: 0.6785714285714286
Recall: 0.5530288461538462
F1 Score: 0.4919242965965873

Overall Metrics Across All Folds (Test Set):
Average Accuracy: 0.5783783783783785
Average Precision: 0.6215931441853944
Average Recall: 0.561625
Average F1 Score: 0.5098512461405627


In [ ]:
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import numpy as np
import pandas as pd
from simpletransformers.classification import ClassificationModel, ClassificationArgs

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5
model_args.learning_rate = 8e-5
model_args.train_batch_size = 8
model_args.eval_batch_size = 8
model_args.max_seq_length = 512

model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "roberta", "roberta-base",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )

    # Train the model using both train_data and val_data
    model.train_model(
        train_data[['text', 'label']],
        eval_df=val_data[['text', 'label']]  # Use val_data for training validation
    )

    # Evaluate the model on the test set (df_test)
    result, model_outputs, _ = model.eval_model(df_test[['text', 'label']])

    # Get true and predicted labels
    true_labels = df_test['label'].values
    predicted_labels = np.argmax(model_outputs, axis=1)

    # Calculate metrics for this fold on df_test
    accuracy = accuracy_score(true_labels, predicted_labels)
    precision = precision_score(true_labels, predicted_labels, average='macro')
    recall = recall_score(true_labels, predicted_labels, average='macro')
    f1 = f1_score(true_labels, predicted_labels, average='macro')

    # Append metrics to lists
    accuracy_scores.append(accuracy)
    precision_scores.append(precision)
    recall_scores.append(recall)
    f1_scores.append(f1)

    print(f"Fold {fold + 1} Metrics on Test Set:")
    print(f"Accuracy: {accuracy}")
    print(f"Precision: {precision}")
    print(f"Recall: {recall}")
    print(f"F1 Score: {f1}")

# Calculate and print average metrics across all folds
print("\nOverall Metrics Across All Folds (Test Set):")
print(f"Average Accuracy: {np.mean(accuracy_scores)}")
print(f"Average Precision: {np.mean(precision_scores)}")
print(f"Average Recall: {np.mean(recall_scores)}")
print(f"Average F1 Score: {np.mean(f1_scores)}")

Starting Fold 1


Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:882: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = amp.GradScaler()


...

0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/10 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


Fold 5 Metrics on Test Set:
Accuracy: 0.3918918918918919
Precision: 0.32074468085106383
Recall: 0.3554807692307692
F1 Score: 0.28028455284552845

Overall Metrics Across All Folds (Test Set):
Average Accuracy: 0.4297297297297297
Average Precision: 0.3991228348205821
Average Recall: 0.40494230769230766
Average F1 Score: 0.37549102307912297


/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


## Combined the data and Display the evaluation metrics

In [ ]:
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import numpy as np
import pandas as pd
from simpletransformers.classification import ClassificationModel, ClassificationArgs

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5
model_args.learning_rate = 3e-5
model_args.train_batch_size = 2
model_args.eval_batch_size = 8
model_args.max_seq_length = 512

model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Concatenate df_train and df_test
df_combined = pd.concat([df_train, df_test], ignore_index=True)

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_combined)):
    print(f"Starting Fold {fold + 1}")

    # Split combined data into train and validation sets
    train_data = df_combined.iloc[train_index]
    val_data = df_combined.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "distilbert", "distilbert-base-uncased",
        num_labels=len(df_combined['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )

    # Train the model using train_data
    model.train_model(
        train_data[['text', 'label']],
        eval_df=val_data[['text', 'label']]  # Use val_data for validation during training
    )

    # Evaluate the model on the validation set (val_data)
    result, model_outputs, _ = model.eval_model(val_data[['text', 'label']])

    # Get true and predicted labels
    true_labels = val_data['label'].values
    predicted_labels = np.argmax(model_outputs, axis=1)

    # Calculate metrics for this fold
    accuracy = accuracy_score(true_labels, predicted_labels)
    precision = precision_score(true_labels, predicted_labels, average='macro')
    recall = recall_score(true_labels, predicted_labels, average='macro')
    f1 = f1_score(true_labels, predicted_labels, average='macro')

    # Append metrics to lists
    accuracy_scores.append(accuracy)
    precision_scores.append(precision)
    recall_scores.append(recall)
    f1_scores.append(f1)

    print(f"Fold {fold + 1} Metrics:")
    print(f"Accuracy: {accuracy}")
    print(f"Precision: {precision}")
    print(f"Recall: {recall}")
    print(f"F1 Score: {f1}")

# Combine the metrics into a DataFrame
metrics_table = pd.DataFrame({
    "Fold": [f"Fold {i+1}" for i in range(len(accuracy_scores))],
    "Accuracy": accuracy_scores,
    "Precision": precision_scores,
    "Recall": recall_scores,
    "F1 Score": f1_scores
})

# Calculate the average metrics and append them to the table
metrics_table.loc["Average"] = [
    "Average",
    np.mean(accuracy_scores),
    np.mean(precision_scores),
    np.mean(recall_scores),
    np.mean(f1_scores)
]

# Print the table
print("\nMetrics Table Across Folds:")
print(metrics_table)

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Starting Fold 1


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


Fold 5 Metrics:
Accuracy: 0.7435897435897436
Precision: 0.7673076923076924
Recall: 0.7261904761904762
F1 Score: 0.7397435897435898

Metrics Table Across Folds:
            Fold  Accuracy  Precision    Recall  F1 Score
0         Fold 1  0.794872   0.782967  0.753175  0.747024
1         Fold 2  0.743590   0.746591  0.728740  0.723058
2         Fold 3  0.794872   0.818182  0.785985  0.794078
3         Fold 4  0.871795   0.905462  0.856250  0.872222
4         Fold 5  0.743590   0.767308  0.726190  0.739744
Average  Average  0.789744   0.804102  0.770068  0.775225


In [ ]:
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import numpy as np
import pandas as pd
from simpletransformers.classification import ClassificationModel, ClassificationArgs

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5
model_args.learning_rate = 8e-5
model_args.train_batch_size = 8
model_args.eval_batch_size = 8
model_args.max_seq_length = 512

model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Concatenate df_train and df_test
df_combined = pd.concat([df_train, df_test], ignore_index=True)

# Separate features (X) and labels (y)
X = df_combined['text'].values
y = df_combined['label'].values

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(X, y)):
    print(f"Starting Fold {fold + 1}")

    # Split combined data into train and validation sets
    train_data = pd.DataFrame({
        "text": X[train_index],
        "label": y[train_index]
    })
    val_data = pd.DataFrame({
        "text": X[val_index],
        "label": y[val_index]
    })

    # Create and train the model
    model = ClassificationModel(
        "roberta", "roberta-base",
        num_labels=len(np.unique(y)),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )

    # Train the model using train_data
    model.train_model(
        train_data,
        eval_df=val_data  # Use val_data for validation during training
    )

    # Evaluate the model on the validation set (val_data)
    result, model_outputs, _ = model.eval_model(val_data)

    # Get true and predicted labels
    true_labels = val_data['label'].values
    predicted_labels = np.argmax(model_outputs, axis=1)

    # Calculate metrics for this fold
    accuracy = accuracy_score(true_labels, predicted_labels)
    precision = precision_score(true_labels, predicted_labels, average='macro')
    recall = recall_score(true_labels, predicted_labels, average='macro')
    f1 = f1_score(true_labels, predicted_labels, average='macro')

    # Append metrics to lists
    accuracy_scores.append(accuracy)
    precision_scores.append(precision)
    recall_scores.append(recall)
    f1_scores.append(f1)

    print(f"Fold {fold + 1} Metrics:")
    print(f"Accuracy: {accuracy}")
    print(f"Precision: {precision}")
    print(f"Recall: {recall}")
    print(f"F1 Score: {f1}")

# Combine the metrics into a DataFrame
metrics_table = pd.DataFrame({
    "Fold": [f"Fold {i+1}" for i in range(len(accuracy_scores))],
    "Accuracy": accuracy_scores,
    "Precision": precision_scores,
    "Recall": recall_scores,
    "F1 Score": f1_scores
})

# Calculate the average metrics and append them to the table
metrics_table.loc["Average"] = [
    "Average",
    np.mean(accuracy_scores),
    np.mean(precision_scores),
    np.mean(recall_scores),
    np.mean(f1_scores)
]

# Print the table
print("\nMetrics Table Across Folds:")
print(metrics_table)

Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Starting Fold 1


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


Fold 5 Metrics:
Accuracy: 0.7435897435897436
Precision: 0.7317765567765567
Recall: 0.7410714285714285
F1 Score: 0.7341329258976318

Metrics Table Across Folds:
            Fold  Accuracy  Precision    Recall  F1 Score
0         Fold 1  0.743590   0.713736  0.702670  0.690476
1         Fold 2  0.538462   0.540640  0.474432  0.428571
2         Fold 3  0.692308   0.517857  0.571402  0.542056
3         Fold 4  0.769231   0.758974  0.766827  0.750345
4         Fold 5  0.743590   0.731777  0.741071  0.734133
Average  Average  0.697436   0.652597  0.651280  0.629116


![Description of Image](https://vitalflux.com/wp-content/uploads/2020/08/Screenshot-2020-08-15-at-11.13.53-AM.png)

## Experiment - Final: DistilBERT

In [23]:
import pandas as pd
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from simpletransformers.classification import ClassificationModel, ClassificationArgs
import numpy as np

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5  # Moderate number of epochs
model_args.learning_rate = 3e-5  # Standard learning rate
model_args.train_batch_size = 2
model_args.eval_batch_size = 8
model_args.max_seq_length = 512
model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
cv_results = []
test_results = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "distilbert", "distilbert-base-uncased",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )
    model.train_model(train_data[['text', 'label']])

    # Evaluate the model on the validation set (val_data)
    val_result, val_model_outputs, _ = model.eval_model(val_data[['text', 'label']])

    # Get true and predicted labels for validation
    val_true_labels = val_data['label'].values
    val_predicted_labels = np.argmax(val_model_outputs, axis=1)

    # Calculate metrics for this fold on validation data
    val_accuracy = accuracy_score(val_true_labels, val_predicted_labels)
    val_precision = precision_score(val_true_labels, val_predicted_labels, average='macro')
    val_recall = recall_score(val_true_labels, val_predicted_labels, average='macro')
    val_f1 = f1_score(val_true_labels, val_predicted_labels, average='macro')

    # Append fold metrics to cv_results
    cv_results.append({
        'Fold': fold + 1,
        'Accuracy': val_accuracy,
        'Precision': val_precision,
        'Recall': val_recall,
        'F1 Score': val_f1
    })

    print(f"Fold {fold + 1} Metrics on Validation Set:")
    print(f"Accuracy: {val_accuracy}")
    print(f"Precision: {val_precision}")
    print(f"Recall: {val_recall}")
    print(f"F1 Score: {val_f1}")

# Train the final model on the entire training set
print("\nTraining final model on the entire training dataset...")
final_model = ClassificationModel(
    "distilbert", "distilbert-base-uncased",
    num_labels=len(df_train['label'].unique()),
    args=model_args,
    use_cuda=True  # Set to False if not using GPU
)
final_model.train_model(df_train[['text', 'label']])

# Evaluate the final model on the test set (df_test)
test_result, test_model_outputs, _ = final_model.eval_model(df_test[['text', 'label']])

# Get true and predicted labels for test set
test_true_labels = df_test['label'].values
test_predicted_labels = np.argmax(test_model_outputs, axis=1)

# Calculate test metrics
test_accuracy = accuracy_score(test_true_labels, test_predicted_labels)
test_precision = precision_score(test_true_labels, test_predicted_labels, average='macro')
test_recall = recall_score(test_true_labels, test_predicted_labels, average='macro')
test_f1 = f1_score(test_true_labels, test_predicted_labels, average='macro')

test_results = {
    'Accuracy': test_accuracy,
    'Precision': test_precision,
    'Recall': test_recall,
    'F1 Score': test_f1
}

print("\nTest Set Metrics:")
print(f"Accuracy: {test_accuracy}")
print(f"Precision: {test_precision}")
print(f"Recall: {test_recall}")
print(f"F1 Score: {test_f1}")

# Convert cross-validation results to DataFrame
cv_results_df = pd.DataFrame(cv_results)

# Calculate average metrics across all folds
average_metrics = {
    'Fold': 'Average',
    'Accuracy': cv_results_df['Accuracy'].mean(),
    'Precision': cv_results_df['Precision'].mean(),
    'Recall': cv_results_df['Recall'].mean(),
    'F1 Score': cv_results_df['F1 Score'].mean()
}

# Convert average metrics to DataFrame and concatenate
average_metrics_df = pd.DataFrame([average_metrics])
cv_results_df = pd.concat([cv_results_df, average_metrics_df], ignore_index=True)

# Display Parameter Table
parameters = {
    'Model': 'DistilBERT',
    'Pretrained Model': 'distilbert-base-uncased',
    'Training Epochs': model_args.num_train_epochs,
    'Learning Rate': model_args.learning_rate,
    'Train Batch Size': model_args.train_batch_size,
    'Eval Batch Size': model_args.eval_batch_size,
    'Max Sequence Length': model_args.max_seq_length,
    'Cross-Validation Folds': kf.n_splits
}
parameters_df = pd.DataFrame(list(parameters.items()), columns=['Parameter', 'Value'])

# Print tables
print("\nModel Parameters:")
print(parameters_df)

print("\nCross-Validation Results:")
print(cv_results_df)

print("\nTest Set Results:")
print(pd.DataFrame([test_results]))

Starting Fold 1


Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:882: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = amp.GradScaler()


...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/10 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():



Test Set Metrics:
Accuracy: 0.7027027027027027
Precision: 0.71875
Recall: 0.7007211538461539
F1 Score: 0.6966518317853457

Model Parameters:
                Parameter                    Value
0                   Model               DistilBERT
1        Pretrained Model  distilbert-base-uncased
2         Training Epochs                        5
3           Learning Rate                  0.00003
4        Train Batch Size                        2
5         Eval Batch Size                        8
6     Max Sequence Length                      512
7  Cross-Validation Folds                        5

Cross-Validation Results:
      Fold  Accuracy  Precision    Recall  F1 Score
0        1  0.692308   0.625947  0.599160  0.595238
1        2  0.789474   0.591346  0.689286  0.631313
2        3  0.710526   0.670913  0.644872  0.630627
3        4  0.684211   0.754545  0.670518  0.665470
4        5  0.763158   0.804167  0.754167  0.768284
5  Average  0.727935   0.689384  0.671600  0.658187

Test Se

## Roberta

In [25]:
import pandas as pd
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from simpletransformers.classification import ClassificationModel, ClassificationArgs
import numpy as np

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5
model_args.learning_rate = 8e-5
model_args.train_batch_size = 8
model_args.eval_batch_size = 8
model_args.max_seq_length = 512
model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
cv_results = []
test_results = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "roberta", "roberta-base",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )
    model.train_model(train_data[['text', 'label']])

    # Evaluate the model on the validation set (val_data)
    val_result, val_model_outputs, _ = model.eval_model(val_data[['text', 'label']])

    # Get true and predicted labels for validation
    val_true_labels = val_data['label'].values
    val_predicted_labels = np.argmax(val_model_outputs, axis=1)

    # Calculate metrics for this fold on validation data
    val_accuracy = accuracy_score(val_true_labels, val_predicted_labels)
    val_precision = precision_score(val_true_labels, val_predicted_labels, average='macro')
    val_recall = recall_score(val_true_labels, val_predicted_labels, average='macro')
    val_f1 = f1_score(val_true_labels, val_predicted_labels, average='macro')

    # Append fold metrics to cv_results
    cv_results.append({
        'Fold': fold + 1,
        'Accuracy': val_accuracy,
        'Precision': val_precision,
        'Recall': val_recall,
        'F1 Score': val_f1
    })

    print(f"Fold {fold + 1} Metrics on Validation Set:")
    print(f"Accuracy: {val_accuracy}")
    print(f"Precision: {val_precision}")
    print(f"Recall: {val_recall}")
    print(f"F1 Score: {val_f1}")

# Train the final model on the entire training set
print("\nTraining final model on the entire training dataset...")
final_model = ClassificationModel(
    "roberta", "roberta-base",
    num_labels=len(df_train['label'].unique()),
    args=model_args,
    use_cuda=True  # Set to False if not using GPU
)
final_model.train_model(df_train[['text', 'label']])

# Evaluate the final model on the test set (df_test)
test_result, test_model_outputs, _ = final_model.eval_model(df_test[['text', 'label']])

# Get true and predicted labels for test set
test_true_labels = df_test['label'].values
test_predicted_labels = np.argmax(test_model_outputs, axis=1)

# Calculate test metrics
test_accuracy = accuracy_score(test_true_labels, test_predicted_labels)
test_precision = precision_score(test_true_labels, test_predicted_labels, average='macro')
test_recall = recall_score(test_true_labels, test_predicted_labels, average='macro')
test_f1 = f1_score(test_true_labels, test_predicted_labels, average='macro')

test_results = {
    'Accuracy': test_accuracy,
    'Precision': test_precision,
    'Recall': test_recall,
    'F1 Score': test_f1
}

print("\nTest Set Metrics:")
print(f"Accuracy: {test_accuracy}")
print(f"Precision: {test_precision}")
print(f"Recall: {test_recall}")
print(f"F1 Score: {test_f1}")

# Convert cross-validation results to DataFrame
cv_results_df = pd.DataFrame(cv_results)

# Calculate average metrics across all folds
average_metrics = {
    'Fold': 'Average',
    'Accuracy': cv_results_df['Accuracy'].mean(),
    'Precision': cv_results_df['Precision'].mean(),
    'Recall': cv_results_df['Recall'].mean(),
    'F1 Score': cv_results_df['F1 Score'].mean()
}

# Convert average metrics to DataFrame and concatenate
average_metrics_df = pd.DataFrame([average_metrics])
cv_results_df = pd.concat([cv_results_df, average_metrics_df], ignore_index=True)

# Display Parameter Table
parameters = {
    'Model': 'Roberta',
    'Pretrained Model': 'roberta-base',
    'Training Epochs': model_args.num_train_epochs,
    'Learning Rate': model_args.learning_rate,
    'Train Batch Size': model_args.train_batch_size,
    'Eval Batch Size': model_args.eval_batch_size,
    'Max Sequence Length': model_args.max_seq_length,
    'Cross-Validation Folds': kf.n_splits
}
parameters_df = pd.DataFrame(list(parameters.items()), columns=['Parameter', 'Value'])

# Print tables
print("\nModel Parameters:")
print(parameters_df)

print("\nCross-Validation Results:")
print(cv_results_df)

print("\nTest Set Results:")
print(pd.DataFrame([test_results]))


Starting Fold 1


Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:882: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = amp.GradScaler()


...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/10 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():



Test Set Metrics:
Accuracy: 0.6621621621621622
Precision: 0.6429597701149425
Recall: 0.6455288461538462
F1 Score: 0.6358120542903152

Model Parameters:
                Parameter         Value
0                   Model       Roberta
1        Pretrained Model  roberta-base
2         Training Epochs             5
3           Learning Rate       0.00008
4        Train Batch Size             8
5         Eval Batch Size             8
6     Max Sequence Length           512
7  Cross-Validation Folds             5

Cross-Validation Results:
      Fold  Accuracy  Precision    Recall  F1 Score
0        1  0.743590   0.711119  0.684874  0.678922
1        2  0.368421   0.092105  0.250000  0.134615
2        3  0.657895   0.619048  0.604468  0.605076
3        4  0.631579   0.521930  0.599495  0.538847
4        5  0.473684   0.260943  0.375000  0.293200
5  Average  0.575034   0.441029  0.502767  0.450132

Test Set Results:
   Accuracy  Precision    Recall  F1 Score
0  0.662162    0.64296  0.645529  

## Albert Model

In [26]:
import pandas as pd
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from simpletransformers.classification import ClassificationModel, ClassificationArgs
import numpy as np

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5  # Moderate number of epochs
model_args.learning_rate = 8e-6  # Start with a standard learning rate
model_args.train_batch_size = 2  # Larger batches for stability
model_args.eval_batch_size = 16  # Match training batch size
model_args.max_seq_length = 512  # Maximum length
model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
cv_results = []
test_results = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "albert", "albert-base-v2",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )
    model.train_model(train_data[['text', 'label']])

    # Evaluate the model on the validation set (val_data)
    val_result, val_model_outputs, _ = model.eval_model(val_data[['text', 'label']])

    # Get true and predicted labels for validation
    val_true_labels = val_data['label'].values
    val_predicted_labels = np.argmax(val_model_outputs, axis=1)

    # Calculate metrics for this fold on validation data
    val_accuracy = accuracy_score(val_true_labels, val_predicted_labels)
    val_precision = precision_score(val_true_labels, val_predicted_labels, average='macro')
    val_recall = recall_score(val_true_labels, val_predicted_labels, average='macro')
    val_f1 = f1_score(val_true_labels, val_predicted_labels, average='macro')

    # Append fold metrics to cv_results
    cv_results.append({
        'Fold': fold + 1,
        'Accuracy': val_accuracy,
        'Precision': val_precision,
        'Recall': val_recall,
        'F1 Score': val_f1
    })

    print(f"Fold {fold + 1} Metrics on Validation Set:")
    print(f"Accuracy: {val_accuracy}")
    print(f"Precision: {val_precision}")
    print(f"Recall: {val_recall}")
    print(f"F1 Score: {val_f1}")

# Train the final model on the entire training set
print("\nTraining final model on the entire training dataset...")
final_model = ClassificationModel(
    "albert", "albert-base-v2",
    num_labels=len(df_train['label'].unique()),
    args=model_args,
    use_cuda=True  # Set to False if not using GPU
)
final_model.train_model(df_train[['text', 'label']])

# Evaluate the final model on the test set (df_test)
test_result, test_model_outputs, _ = final_model.eval_model(df_test[['text', 'label']])

# Get true and predicted labels for test set
test_true_labels = df_test['label'].values
test_predicted_labels = np.argmax(test_model_outputs, axis=1)

# Calculate test metrics
test_accuracy = accuracy_score(test_true_labels, test_predicted_labels)
test_precision = precision_score(test_true_labels, test_predicted_labels, average='macro')
test_recall = recall_score(test_true_labels, test_predicted_labels, average='macro')
test_f1 = f1_score(test_true_labels, test_predicted_labels, average='macro')

test_results = {
    'Accuracy': test_accuracy,
    'Precision': test_precision,
    'Recall': test_recall,
    'F1 Score': test_f1
}

print("\nTest Set Metrics:")
print(f"Accuracy: {test_accuracy}")
print(f"Precision: {test_precision}")
print(f"Recall: {test_recall}")
print(f"F1 Score: {test_f1}")

# Convert cross-validation results to DataFrame
cv_results_df = pd.DataFrame(cv_results)

# Calculate average metrics across all folds
average_metrics = {
    'Fold': 'Average',
    'Accuracy': cv_results_df['Accuracy'].mean(),
    'Precision': cv_results_df['Precision'].mean(),
    'Recall': cv_results_df['Recall'].mean(),
    'F1 Score': cv_results_df['F1 Score'].mean()
}

# Convert average metrics to DataFrame and concatenate
average_metrics_df = pd.DataFrame([average_metrics])
cv_results_df = pd.concat([cv_results_df, average_metrics_df], ignore_index=True)

# Display Parameter Table
parameters = {
    'Model': 'Albert',
    'Pretrained Model': 'albert-base-v2',
    'Training Epochs': model_args.num_train_epochs,
    'Learning Rate': model_args.learning_rate,
    'Train Batch Size': model_args.train_batch_size,
    'Eval Batch Size': model_args.eval_batch_size,
    'Max Sequence Length': model_args.max_seq_length,
    'Cross-Validation Folds': kf.n_splits
}
parameters_df = pd.DataFrame(list(parameters.items()), columns=['Parameter', 'Value'])

# Print tables
print("\nModel Parameters:")
print(parameters_df)

print("\nCross-Validation Results:")
print(cv_results_df)

print("\nTest Set Results:")
print(pd.DataFrame([test_results]))


Starting Fold 1


config.json:   0%|          | 0.00/684 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/47.4M [00:00<?, ?B/s]

Some weights of AlbertForSequenceClassification were not initialized from the model checkpoint at albert-base-v2 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():



Test Set Metrics:
Accuracy: 0.6486486486486487
Precision: 0.6279761904761905
Recall: 0.6120673076923077
F1 Score: 0.5931818181818181

Model Parameters:
                Parameter           Value
0                   Model          Albert
1        Pretrained Model  albert-base-v2
2         Training Epochs               5
3           Learning Rate        0.000008
4        Train Batch Size               2
5         Eval Batch Size              16
6     Max Sequence Length             512
7  Cross-Validation Folds               5

Cross-Validation Results:
      Fold  Accuracy  Precision    Recall  F1 Score
0        1  0.692308   0.729221  0.578151  0.585264
1        2  0.763158   0.582589  0.657143  0.606763
2        3  0.631579   0.484821  0.535742  0.501741
3        4  0.500000   0.505263  0.489268  0.415934
4        5  0.763158   0.812937  0.675000  0.686667
5  Average  0.670040   0.622966  0.587061  0.559274

Test Set Results:
   Accuracy  Precision    Recall  F1 Score
0  0.648649   0.

## BERT

In [25]:
import pandas as pd
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from simpletransformers.classification import ClassificationModel, ClassificationArgs
import numpy as np

# Define your ClassificationModel args
model_args = ClassificationArgs()
model_args.num_train_epochs = 5
model_args.learning_rate = 8e-6
model_args.train_batch_size = 1
model_args.eval_batch_size = 16
model_args.max_seq_length = 512
model_args.output_dir = "outputs/"
model_args.overwrite_output_dir = True

# Define 5-Fold Cross-Validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Initialize lists to store metrics
cv_results = []
test_results = []

# Perform K-Fold Cross-Validation
for fold, (train_index, val_index) in enumerate(kf.split(df_train)):
    print(f"Starting Fold {fold + 1}")

    # Split into train and validation sets for this fold
    train_data = df_train.iloc[train_index]
    val_data = df_train.iloc[val_index]

    # Create and train the model
    model = ClassificationModel(
        "bert", "bert-base-uncased",
        num_labels=len(df_train['label'].unique()),  # Number of unique labels
        args=model_args,
        use_cuda=True  # Set to False if not using GPU
    )
    model.train_model(train_data[['text', 'label']])

    # Evaluate the model on the validation set (val_data)
    val_result, val_model_outputs, _ = model.eval_model(val_data[['text', 'label']])

    # Get true and predicted labels for validation
    val_true_labels = val_data['label'].values
    val_predicted_labels = np.argmax(val_model_outputs, axis=1)

    # Calculate metrics for this fold on validation data
    val_accuracy = accuracy_score(val_true_labels, val_predicted_labels)
    val_precision = precision_score(val_true_labels, val_predicted_labels, average='macro')
    val_recall = recall_score(val_true_labels, val_predicted_labels, average='macro')
    val_f1 = f1_score(val_true_labels, val_predicted_labels, average='macro')

    # Append fold metrics to cv_results
    cv_results.append({
        'Fold': fold + 1,
        'Accuracy': val_accuracy,
        'Precision': val_precision,
        'Recall': val_recall,
        'F1 Score': val_f1
    })

    print(f"Fold {fold + 1} Metrics on Validation Set:")
    print(f"Accuracy: {val_accuracy}")
    print(f"Precision: {val_precision}")
    print(f"Recall: {val_recall}")
    print(f"F1 Score: {val_f1}")

# Train the final model on the entire training set
print("\nTraining final model on the entire training dataset...")
final_model = ClassificationModel(
    "bert", "bert-base-uncased",
    num_labels=len(df_train['label'].unique()),
    args=model_args,
    use_cuda=True  # Set to False if not using GPU
)
final_model.train_model(df_train[['text', 'label']])

# Evaluate the final model on the test set (df_test)
test_result, test_model_outputs, _ = final_model.eval_model(df_test[['text', 'label']])

# Get true and predicted labels for test set
test_true_labels = df_test['label'].values
test_predicted_labels = np.argmax(test_model_outputs, axis=1)

# Calculate test metrics
test_accuracy = accuracy_score(test_true_labels, test_predicted_labels)
test_precision = precision_score(test_true_labels, test_predicted_labels, average='macro')
test_recall = recall_score(test_true_labels, test_predicted_labels, average='macro')
test_f1 = f1_score(test_true_labels, test_predicted_labels, average='macro')

test_results = {
    'Accuracy': test_accuracy,
    'Precision': test_precision,
    'Recall': test_recall,
    'F1 Score': test_f1
}

print("\nTest Set Metrics:")
print(f"Accuracy: {test_accuracy}")
print(f"Precision: {test_precision}")
print(f"Recall: {test_recall}")
print(f"F1 Score: {test_f1}")

# Convert cross-validation results to DataFrame
cv_results_df = pd.DataFrame(cv_results)

# Calculate average metrics across all folds
average_metrics = {
    'Fold': 'Average',
    'Accuracy': cv_results_df['Accuracy'].mean(),
    'Precision': cv_results_df['Precision'].mean(),
    'Recall': cv_results_df['Recall'].mean(),
    'F1 Score': cv_results_df['F1 Score'].mean()
}

# Convert average metrics to DataFrame and concatenate
average_metrics_df = pd.DataFrame([average_metrics])
cv_results_df = pd.concat([cv_results_df, average_metrics_df], ignore_index=True)

# Display Parameter Table
parameters = {
    'Model': 'bert-base',
    'Pretrained Model': 'bert-base-uncased',
    'Training Epochs': model_args.num_train_epochs,
    'Learning Rate': model_args.learning_rate,
    'Train Batch Size': model_args.train_batch_size,
    'Eval Batch Size': model_args.eval_batch_size,
    'Max Sequence Length': model_args.max_seq_length,
    'Cross-Validation Folds': kf.n_splits
}
parameters_df = pd.DataFrame(list(parameters.items()), columns=['Parameter', 'Value'])

# Print tables
print("\nModel Parameters:")
print(parameters_df)

print("\nCross-Validation Results:")
print(cv_results_df)

print("\nTest Set Results:")
print(pd.DataFrame([test_results]))


Starting Fold 1


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:610: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:882: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = amp.GradScaler()


...

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1453: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


0it [00:00, ?it/s]

Running Evaluation:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1505: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():



Test Set Metrics:
Accuracy: 0.581081081081081
Precision: 0.5666754756871035
Recall: 0.5336057692307692
F1 Score: 0.4758978328173375

Model Parameters:
                Parameter              Value
0                   Model          bert-base
1        Pretrained Model  bert-base-uncased
2         Training Epochs                  5
3           Learning Rate           0.000008
4        Train Batch Size                  1
5         Eval Batch Size                 16
6     Max Sequence Length                512
7  Cross-Validation Folds                  5

Cross-Validation Results:
      Fold  Accuracy  Precision    Recall  F1 Score
0        1  0.717949   0.781822  0.592437  0.604136
1        2  0.789474   0.589744  0.682143  0.628683
2        3  0.710526   0.533613  0.596931  0.556250
3        4  0.657895   0.525210  0.627273  0.549548
4        5  0.710526   0.769697  0.670833  0.695046
5  Average  0.717274   0.640017  0.633923  0.606733

Test Set Results:
   Accuracy  Precision    Recall 

### Model Comparison and Parameters

| Model          | Pretrained Model         | Test Accuracy | Test Precision | Test Recall | Test F1 Score | CV Average Accuracy | CV Average Precision | CV Average Recall | CV Average F1 Score | Parameters                                          |
|----------------|--------------------------|---------------|----------------|-------------|---------------|---------------------|----------------------|-------------------|---------------------|----------------------------------------------------|
| Roberta        | roberta-base             | 0.6622        | 0.6430         | 0.6455      | 0.6358        | 0.5750              | 0.4410               | 0.5028            | 0.4501              | Epochs: 5, LR: 0.00008, Train Batch: 8, Eval Batch: 8, Max Seq Len: 512 |
| Albert         | albert-base-v2           | 0.6486        | 0.6280         | 0.6121      | 0.5932        | 0.6700              | 0.6230               | 0.5871            | 0.5593              | Epochs: 5, LR: 0.000008, Train Batch: 2, Eval Batch: 16, Max Seq Len: 512 |
| BERT           | bert-base-uncased        | 0.5811        | 0.5667         | 0.5336      | 0.4759        | 0.7173              | 0.6400               | 0.6339            | 0.6067              | Epochs: 5, LR: 0.000008, Train Batch: 1, Eval Batch: 16, Max Seq Len: 512 |
| **DistilBERT** | **distilbert-base-uncased** | **0.7027**   | **0.7188**    | **0.7007**  | **0.6967**    | **0.7279**          | **0.6894**           | **0.6716**        | **0.6582**          | **Epochs: 5, LR: 0.00003, Train Batch: 2, Eval Batch: 8, Max Seq Len: 512** |

### Key:
- **Bolded Values**: Indicates the best model for each metric.